In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [2]:
writer = SummaryWriter()

In [3]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [4]:
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14393, 4096) (14393, 1) (3599, 4096) (3599, 1)


In [5]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [6]:
train_set = train_set.reshape((-1,1,64,64))
test_set = test_set.reshape((-1,1,64,64))
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 1, 64, 64) (14392, 1) (3598, 1, 64, 64) (3598, 1)


In [7]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)

print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 1, 64, 64) (14392,) (3598, 1, 64, 64) (3598,)


In [8]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [9]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [10]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [11]:
# Convolutional neural network (two convolutional layers)
class CNN(nn.Module):
    def __init__(self, num_classes=4):
        super(CNN, self).__init__()
        self.c1 = nn.Conv2d(1, 32, kernel_size=3, stride=1, padding='same')
        self.c2 = nn.Conv2d(32, 32, kernel_size=3, stride=1, padding='same')
        self.c3 = nn.Conv2d(64, 64, kernel_size=3, stride=1, padding='same')
        self.c4 = nn.Conv2d(64, 64, kernel_size=3, stride=1, padding='valid')
        self.c5 = nn.Conv2d(64, 64, kernel_size=3, stride=1, padding='same')
        self.c6 = nn.Conv2d(128, 128, kernel_size=3, stride=1, padding='same')
        
        self.d1 = nn.Dropout(p=0.25)
        self.d2 = nn.Dropout(p=0.25)
        self.d3 = nn.Dropout(p=0.25)
        self.d4 = nn.Dropout(p=0.25)
        
        self.bn1 =  nn.BatchNorm2d(32)
        self.bn2 =  nn.BatchNorm2d(64)
        self.bn3 =  nn.BatchNorm2d(64)
        
        self.fc1 = nn.Linear(15*15*128, 512)
        self.fc2 = nn.Linear(512, num_classes)
        
        
    def forward(self, x):
        out1 = F.leaky_relu(self.c1(x),0.2)
        out1 = self.d1(out1)
        
        out2 = self.c2(out1)
        out2 = F.leaky_relu(self.bn1(out2))
        
        out = torch.cat((out1, out2), dim=1)
        out = self.c3(out)
        out = F.leaky_relu(out,0.2)
        out = self.d2(out)
        
        out = F.max_pool2d(out, kernel_size=2, stride=2)
        
        out3 = self.c4(out)
        out3 = F.leaky_relu(self.bn2(out3),0.2)
        out3 = self.d3(out3)
        
        out4 = self.c5(out3)
        out4 = F.leaky_relu(self.bn3(out4),0.2)
        
        out = torch.cat((out3, out4), dim=1)
        out = self.c6(out)
        out = F.leaky_relu(out,0.2)
        out = self.d3(out)
        
        out = F.max_pool2d(out, kernel_size=2, stride=2)
        
        out = out.reshape(out.size(0), -1)
        
        out = self.fc1(out)
        out = F.leaky_relu(out,0.2)
        out = self.d4(out)
        
        out = self.fc2(out)
        
        return out

In [12]:
model = CNN(num_classes).to(device)

In [13]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [14]:
def train():
    # Train the model
    total_step = len(train_loader)
    for epoch in range(num_epochs):
        correct=0
        total=0
        running_loss = 0
        for i, (X, Y) in enumerate(train_loader):
            X = X.to(device)
            Y = Y.to(device)


            # Forward pass
            outputs = model(X)
            loss = criterion(outputs, Y)

            # Backward and optimize
            optimizer.zero_grad()
            loss.backward()
            #scheduler.step() 
            #print(scheduler.get_last_lr()[0])

            optimizer.step()
            scheduler.step() 
            #print(optimizer.param_groups[0]["lr"])

            _, predicted = outputs.max(1)
            total += Y.size(0)
            correct += predicted.eq(Y).sum().item()
            running_loss += loss.item()
            accu=100.*correct/total
            train_loss = running_loss/(i+1)
            print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))


            #writer.add_scalar(f'train/accuracy', accu, epoch)
            #writer.add_scalar(f'train/loss', train_loss, epoch)
            writer.add_scalars(f'train/accuracy_loss', {
                'accuracy': accu,
                'loss': train_loss,
            }, epoch)
        
        

0.001
Epoch [1/300], Step [1/225], Training Accuracy: 35.9375%, Training Loss: 1.3860%
0.001
Epoch [1/300], Step [2/225], Training Accuracy: 28.1250%, Training Loss: 15.1225%
0.001
Epoch [1/300], Step [3/225], Training Accuracy: 26.0417%, Training Loss: 13.9029%
0.001
Epoch [1/300], Step [4/225], Training Accuracy: 26.5625%, Training Loss: 10.9293%
0.001
Epoch [1/300], Step [5/225], Training Accuracy: 27.5000%, Training Loss: 9.5791%
0.001
Epoch [1/300], Step [6/225], Training Accuracy: 25.7812%, Training Loss: 8.9962%
0.001
Epoch [1/300], Step [7/225], Training Accuracy: 25.6696%, Training Loss: 8.2697%
0.001
Epoch [1/300], Step [8/225], Training Accuracy: 25.0000%, Training Loss: 7.5742%
0.001
Epoch [1/300], Step [9/225], Training Accuracy: 25.0000%, Training Loss: 7.3103%
0.001
Epoch [1/300], Step [10/225], Training Accuracy: 25.4688%, Training Loss: 6.9672%
0.001
Epoch [1/300], Step [11/225], Training Accuracy: 25.0000%, Training Loss: 6.6907%
0.001
Epoch [1/300], Step [12/225], Tr

0.001
Epoch [1/300], Step [95/225], Training Accuracy: 27.2533%, Training Loss: 2.3196%
0.001
Epoch [1/300], Step [96/225], Training Accuracy: 27.2949%, Training Loss: 2.3100%
0.001
Epoch [1/300], Step [97/225], Training Accuracy: 27.3840%, Training Loss: 2.3000%
0.001
Epoch [1/300], Step [98/225], Training Accuracy: 27.4713%, Training Loss: 2.2907%
0.001
Epoch [1/300], Step [99/225], Training Accuracy: 27.5095%, Training Loss: 2.2813%
0.001
Epoch [1/300], Step [100/225], Training Accuracy: 27.5781%, Training Loss: 2.2725%
0.001
Epoch [1/300], Step [101/225], Training Accuracy: 27.6764%, Training Loss: 2.2640%
0.001
Epoch [1/300], Step [102/225], Training Accuracy: 27.6654%, Training Loss: 2.2565%
0.001
Epoch [1/300], Step [103/225], Training Accuracy: 27.7306%, Training Loss: 2.2476%
0.001
Epoch [1/300], Step [104/225], Training Accuracy: 27.8245%, Training Loss: 2.2383%
0.001
Epoch [1/300], Step [105/225], Training Accuracy: 27.9018%, Training Loss: 2.2302%
0.001
Epoch [1/300], Step 

0.001
Epoch [1/300], Step [193/225], Training Accuracy: 29.9790%, Training Loss: 1.8366%
0.001
Epoch [1/300], Step [194/225], Training Accuracy: 29.9855%, Training Loss: 1.8339%
0.001
Epoch [1/300], Step [195/225], Training Accuracy: 30.0000%, Training Loss: 1.8312%
0.001
Epoch [1/300], Step [196/225], Training Accuracy: 29.9665%, Training Loss: 1.8290%
0.001
Epoch [1/300], Step [197/225], Training Accuracy: 29.9492%, Training Loss: 1.8266%
0.001
Epoch [1/300], Step [198/225], Training Accuracy: 29.9716%, Training Loss: 1.8238%
0.001
Epoch [1/300], Step [199/225], Training Accuracy: 29.9623%, Training Loss: 1.8213%
0.001
Epoch [1/300], Step [200/225], Training Accuracy: 29.9766%, Training Loss: 1.8189%
0.001
Epoch [1/300], Step [201/225], Training Accuracy: 30.0295%, Training Loss: 1.8162%
0.001
Epoch [1/300], Step [202/225], Training Accuracy: 30.0124%, Training Loss: 1.8141%
0.001
Epoch [1/300], Step [203/225], Training Accuracy: 29.9877%, Training Loss: 1.8123%
0.001
Epoch [1/300], 

0.001
Epoch [2/300], Step [61/225], Training Accuracy: 36.4754%, Training Loss: 1.3020%
0.001
Epoch [2/300], Step [62/225], Training Accuracy: 36.5171%, Training Loss: 1.3016%
0.001
Epoch [2/300], Step [63/225], Training Accuracy: 36.5575%, Training Loss: 1.3017%
0.001
Epoch [2/300], Step [64/225], Training Accuracy: 36.5234%, Training Loss: 1.3033%
0.001
Epoch [2/300], Step [65/225], Training Accuracy: 36.6106%, Training Loss: 1.3028%
0.001
Epoch [2/300], Step [66/225], Training Accuracy: 36.7424%, Training Loss: 1.3026%
0.001
Epoch [2/300], Step [67/225], Training Accuracy: 36.8237%, Training Loss: 1.3014%
0.001
Epoch [2/300], Step [68/225], Training Accuracy: 36.8566%, Training Loss: 1.3004%
0.001
Epoch [2/300], Step [69/225], Training Accuracy: 36.7301%, Training Loss: 1.3001%
0.001
Epoch [2/300], Step [70/225], Training Accuracy: 36.6964%, Training Loss: 1.3003%
0.001
Epoch [2/300], Step [71/225], Training Accuracy: 36.7298%, Training Loss: 1.3006%
0.001
Epoch [2/300], Step [72/22

0.001
Epoch [2/300], Step [159/225], Training Accuracy: 37.5098%, Training Loss: 1.2872%
0.001
Epoch [2/300], Step [160/225], Training Accuracy: 37.5195%, Training Loss: 1.2867%
0.001
Epoch [2/300], Step [161/225], Training Accuracy: 37.5970%, Training Loss: 1.2855%
0.001
Epoch [2/300], Step [162/225], Training Accuracy: 37.6543%, Training Loss: 1.2847%
0.001
Epoch [2/300], Step [163/225], Training Accuracy: 37.6438%, Training Loss: 1.2844%
0.001
Epoch [2/300], Step [164/225], Training Accuracy: 37.6905%, Training Loss: 1.2845%
0.001
Epoch [2/300], Step [165/225], Training Accuracy: 37.6705%, Training Loss: 1.2847%
0.001
Epoch [2/300], Step [166/225], Training Accuracy: 37.6224%, Training Loss: 1.2849%
0.001
Epoch [2/300], Step [167/225], Training Accuracy: 37.6778%, Training Loss: 1.2842%
0.001
Epoch [2/300], Step [168/225], Training Accuracy: 37.6488%, Training Loss: 1.2839%
0.001
Epoch [2/300], Step [169/225], Training Accuracy: 37.7034%, Training Loss: 1.2830%
0.001
Epoch [2/300], 

...

Epoch [299/300], Step [33/225], Training Accuracy: 99.7159%, Training Loss: 0.0126%
3.125e-05
Epoch [299/300], Step [34/225], Training Accuracy: 99.7243%, Training Loss: 0.0126%
3.125e-05
Epoch [299/300], Step [35/225], Training Accuracy: 99.7321%, Training Loss: 0.0127%
3.125e-05
Epoch [299/300], Step [36/225], Training Accuracy: 99.7396%, Training Loss: 0.0125%
3.125e-05
Epoch [299/300], Step [37/225], Training Accuracy: 99.7466%, Training Loss: 0.0124%
3.125e-05
Epoch [299/300], Step [38/225], Training Accuracy: 99.7533%, Training Loss: 0.0124%
3.125e-05
Epoch [299/300], Step [39/225], Training Accuracy: 99.7596%, Training Loss: 0.0124%
3.125e-05
Epoch [299/300], Step [40/225], Training Accuracy: 99.7656%, Training Loss: 0.0124%
3.125e-05
Epoch [299/300], Step [41/225], Training Accuracy: 99.7332%, Training Loss: 0.0130%
3.125e-05
Epoch [299/300], Step [42/225], Training Accuracy: 99.7396%, Training Loss: 0.0128%
3.125e-05
Epoch [299/300], Step [43/225], Training Accuracy: 99.7456%,

3.125e-05
Epoch [299/300], Step [125/225], Training Accuracy: 99.8125%, Training Loss: 0.0117%
3.125e-05
Epoch [299/300], Step [126/225], Training Accuracy: 99.8140%, Training Loss: 0.0118%
3.125e-05
Epoch [299/300], Step [127/225], Training Accuracy: 99.8155%, Training Loss: 0.0118%
3.125e-05
Epoch [299/300], Step [128/225], Training Accuracy: 99.8169%, Training Loss: 0.0118%
3.125e-05
Epoch [299/300], Step [129/225], Training Accuracy: 99.8183%, Training Loss: 0.0118%
3.125e-05
Epoch [299/300], Step [130/225], Training Accuracy: 99.8197%, Training Loss: 0.0118%
3.125e-05
Epoch [299/300], Step [131/225], Training Accuracy: 99.8211%, Training Loss: 0.0118%
3.125e-05
Epoch [299/300], Step [132/225], Training Accuracy: 99.8224%, Training Loss: 0.0118%
3.125e-05
Epoch [299/300], Step [133/225], Training Accuracy: 99.8238%, Training Loss: 0.0118%
3.125e-05
Epoch [299/300], Step [134/225], Training Accuracy: 99.8251%, Training Loss: 0.0119%
3.125e-05
Epoch [299/300], Step [135/225], Trainin

3.125e-05
Epoch [299/300], Step [217/225], Training Accuracy: 99.8488%, Training Loss: 0.0111%
3.125e-05
Epoch [299/300], Step [218/225], Training Accuracy: 99.8495%, Training Loss: 0.0111%
3.125e-05
Epoch [299/300], Step [219/225], Training Accuracy: 99.8430%, Training Loss: 0.0111%
3.125e-05
Epoch [299/300], Step [220/225], Training Accuracy: 99.8438%, Training Loss: 0.0111%
3.125e-05
Epoch [299/300], Step [221/225], Training Accuracy: 99.8303%, Training Loss: 0.0112%
3.125e-05
Epoch [299/300], Step [222/225], Training Accuracy: 99.8311%, Training Loss: 0.0112%
3.125e-05
Epoch [299/300], Step [223/225], Training Accuracy: 99.8318%, Training Loss: 0.0112%
3.125e-05
Epoch [299/300], Step [224/225], Training Accuracy: 99.8326%, Training Loss: 0.0112%
3.125e-05
Epoch [299/300], Step [225/225], Training Accuracy: 99.8332%, Training Loss: 0.0112%
3.125e-05
Epoch [300/300], Step [1/225], Training Accuracy: 100.0000%, Training Loss: 0.0158%
3.125e-05
Epoch [300/300], Step [2/225], Training A

3.125e-05
Epoch [300/300], Step [84/225], Training Accuracy: 99.8326%, Training Loss: 0.0112%
3.125e-05
Epoch [300/300], Step [85/225], Training Accuracy: 99.8346%, Training Loss: 0.0112%
3.125e-05
Epoch [300/300], Step [86/225], Training Accuracy: 99.8365%, Training Loss: 0.0111%
3.125e-05
Epoch [300/300], Step [87/225], Training Accuracy: 99.8384%, Training Loss: 0.0111%
3.125e-05
Epoch [300/300], Step [88/225], Training Accuracy: 99.8402%, Training Loss: 0.0110%
3.125e-05
Epoch [300/300], Step [89/225], Training Accuracy: 99.8244%, Training Loss: 0.0112%
3.125e-05
Epoch [300/300], Step [90/225], Training Accuracy: 99.8264%, Training Loss: 0.0111%
3.125e-05
Epoch [300/300], Step [91/225], Training Accuracy: 99.8283%, Training Loss: 0.0111%
3.125e-05
Epoch [300/300], Step [92/225], Training Accuracy: 99.8302%, Training Loss: 0.0111%
3.125e-05
Epoch [300/300], Step [93/225], Training Accuracy: 99.8320%, Training Loss: 0.0110%
3.125e-05
Epoch [300/300], Step [94/225], Training Accuracy:

3.125e-05
Epoch [300/300], Step [171/225], Training Accuracy: 99.8355%, Training Loss: 0.0114%
3.125e-05
Epoch [300/300], Step [172/225], Training Accuracy: 99.8365%, Training Loss: 0.0115%
3.125e-05
Epoch [300/300], Step [173/225], Training Accuracy: 99.8374%, Training Loss: 0.0115%
3.125e-05
Epoch [300/300], Step [174/225], Training Accuracy: 99.8384%, Training Loss: 0.0114%
3.125e-05
Epoch [300/300], Step [175/225], Training Accuracy: 99.8214%, Training Loss: 0.0116%
3.125e-05
Epoch [300/300], Step [176/225], Training Accuracy: 99.8224%, Training Loss: 0.0116%
3.125e-05
Epoch [300/300], Step [177/225], Training Accuracy: 99.8234%, Training Loss: 0.0116%
3.125e-05
Epoch [300/300], Step [178/225], Training Accuracy: 99.8244%, Training Loss: 0.0116%
3.125e-05
Epoch [300/300], Step [179/225], Training Accuracy: 99.8254%, Training Loss: 0.0116%
3.125e-05
Epoch [300/300], Step [180/225], Training Accuracy: 99.8177%, Training Loss: 0.0116%
3.125e-05
Epoch [300/300], Step [181/225], Trainin

In [16]:
def test():
    # Test the model
    model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
    with torch.no_grad():
        correct = 0
        total = 0
        for X, Y in test_loader:
            X = X.to(device)
            Y = Y.to(device)
            outputs = model(X)
            _, predicted = torch.max(outputs.data, 1)
            total += Y.size(0)
            correct += (predicted == Y).sum().item()

        print('Test Accuracy : {} %'.format(100 * correct / total))

    # Save the model checkpoint
    #torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 71.15063924402446 %


In [ ]:
#for i in range(10):
#    x = all_data[i]
#    y = all_label[all-i]